In [1]:
import pandas as pd
from pyecharts.charts import Line, Bar, Map, Timeline
from pyecharts import options as opts

from pyecharts.globals import CurrentConfig, NotebookType
CurrentConfig.NOTEBOOK_TYPE = NotebookType.JUPYTER_LAB

In [2]:
df = pd.read_csv('data/daily_confirmed.csv')
df.set_index(pd.to_datetime(df['日期']), inplace=True)

In [3]:
print('Data Amount:', df.shape[0])
print('Data Time Range:', df.index.min().date(), df.index.max().date())

Data Amount: 247
Data Time Range: 2020-01-20 2020-09-22


In [4]:
df.head(3)

日期   湖北  香港  广东  浙江  河南  湖南  安徽  上海  黑龙江  ...  海南  甘肃  吉林  \
日期                                                           ...               
2020-01-20  2020-1-20  270   0  14   0   0   0   0   1    0  ...   0   0   0   
2020-01-21  2020-1-21  375   0  23   5   1   1   0   9    0  ...   0   0   0   
2020-01-22  2020-1-22  444   1  32  27   5   9   4  16    1  ...   4   0   0   

            贵州  宁夏  澳门  青海  西藏  累计确诊  每日新增  
日期                                          
2020-01-20   0   0   0   0   0   290   290  
2020-01-21   0   0   0   0   0   435   145  
2020-01-22   1   1   1   0   0   588   153  

[3 rows x 37 columns]

In [5]:
def addDailyMap(df) -> Map:
    province = df.index.values[1:-2].tolist()
    values = df.values[1:-2].astype('int').tolist()
    date = df.values[0]
    m = (
        Map(
            init_opts=opts.InitOpts()
        )
        .add('Cumculative Confirmed', [list(z) for z in zip(province, values)], 'china', is_map_symbol_show=False)
        .set_series_opts(label_opts=opts.LabelOpts(is_show=True))
        .set_global_opts(
            title_opts=opts.TitleOpts(title='Cumulative number of confirmed COVID-19 in China over provinces', subtitle=date, pos_left='center'),
            legend_opts=opts.LegendOpts(is_show=False),
            visualmap_opts=opts.VisualMapOpts(
                is_piecewise=True,
                pieces=[
                    {"max": 100, "color": '#ffeead', 'label': 'less than 100'},
                    {"min": 100, "max": 500, 'color': '#f29c2b', 'label': '100-500'},
                    {"min": 500, "max": 1000, 'color': '#d9534f', 'label': '500-1000'},
                    {"min": 1000, "max": 2000, "color":'#de4307', 'label': '1000-2000'},
                    {"min": 2000, 'color': '#dd0a35', 'label': 'above 2000'}
                ]
            )
        )
    )
    return m

In [6]:
def getMapTimeline(df):
    t = (
        Timeline(init_opts=opts.InitOpts())
        .add_schema(play_interval=500)
    )
    for date in df.index:
        t.add(addDailyMap(df.loc[date]), date.date())
    return t

In [7]:
t = getMapTimeline(df)
t.load_javascript()

In [8]:
t.render('render/Accumulated diagnosis map.html')

'D:\\编程\\lab\\Data Mining\\render\\Accumulated diagnosis map.html'

In [9]:
t.render_notebook()

# 通过交互分析可以发现：

## 现存确诊人数图

- 在1.20日左右，全国公布的疫情一开始出现在广东、湖北、北京上海等地，此时湖北的疫情确诊人数已经突破200；
- 此后，疫情从湖北开始向四周身份成扩散趋势，在1.26日湖北的确诊人数已经突破1000；除湖北外，浙江与广东确诊人数也到达三位数；国外在美国、澳大利亚、法国和泰国等东南亚国家也出现确诊病例；
- 在2.2日前后，湖北的确诊人数突破五位数，其他地区疫情人数继续增加；国外疫情也在欧洲、东南亚、美洲呈缓慢扩散趋势
- 在2月中旬，西藏成为国内首个清零的省份；国外继续缓慢增长；国内疫情迎来拐点，现存确诊人数趋于平缓、不再增加，并开始缓慢减少；现存确诊人数约为50000左右，其中大部分集中在湖北；
二月底三月初，国内确诊人数逐渐减少，国外此时开始大规模出现感染并扩散到多个国家；此时意大利、伊朗疫情较为严重；疫情开始扩散到非洲、南美洲；
三月中旬后，国内疫情已经基本得到控制，大多省份恢复到个位数或清零，绝大多数现存确诊病例集中在湖北；而世界上大部分国家都已出现确诊报告，许多国家突破五位数确诊；其中欧洲和伊朗、美国较为严重；
四月初，国内确诊人数继续减少，但有部分省份出现略微反扑；国外疫情几乎已经扩散到世界所有国家，其中美国确诊人数已经突破20万，是世界最严重的地区；
从四月中旬开始，由于外来输入原因，国内黑龙江及东北地区出现了一次比较严重的疫情反扑，确诊人数接近500，但在五月初逐步得到控制；
国外疫情在四五月份继续趋向严重，在5.8美国的确诊人数突破百万；但部分早期疫情严重的国家由于采取了有效的控制手段导致疫情缓解；

## 累计死亡人数

二月初，世界各国开始出现死亡病例；
国内的死亡病例数在二月中旬趋向平缓；
在三月中旬，世界各国死亡病例陆续出现或开始明显增多；
在五月份，报告的死亡数以美国、欧洲最为严重，许多国家死亡人数已经远远超过了中国；

## 死亡率：

死亡率也可以反应出疫情的控制程度，死亡率越低表明患者得到救治的概率越大；
在医疗资源充足的地区，死亡率可以降低到1%左右；医疗资源不足的地区，死亡率可以高达10%；
国内死亡率数据分析：
在一月下旬，中国的死亡率以黑龙江、湖北、湖南河南较为严重，但在一月底二月初除湖北外，其他省份呈下降趋势；
在国内疫情确诊人数峰值的二月中旬，国内平均死亡率为2.5，死亡率相对较高的是湖北、黑龙江、海南、台湾等地；
此后，国内湖北的死亡率继续升高，可能是由于医疗资源不足，无法给予患者有效救治，同时此前积累的确诊患者也陆续出现死亡；同样升高的有新疆、黑龙江；
三月中旬后，在国内疫情基本得到控制的情况下，全国平均死亡率在4%，湖北死亡率达到4.7左右；
在四月中旬补统计了一下之前因为新冠去世但未计入死亡率数据的死亡人数，最后湖北的死亡率为6.6，国内平均死亡率在5.5
国外死亡率数据分析：
从三月下旬开始，伴随着疫情的大规模扩散，各国疫情死亡率也逐步增高；
值得注意的是，许多国家的统计数据表明在其疫情刚开始出现的数日内死亡率是一个高峰，可能表明了在初始阶段未能对患者作出良好的检测和发现，只能从新冠重症患者处得到资料；
虽然非洲等某些不发达国家的疫情报告数据较少，但死亡率较高；可能表明了对于新冠的轻症患者，并没有良好的检测能力；
死亡率较高的国家显著集中在欧洲地区，表明了医疗资源的相对短缺；墨西哥的死亡率也较高；
总体来看：

中国在三月份就逐步控制住了疫情趋势，为世界抗疫事业做出了卓越的典范；
欧洲和美洲等发达国家疫情数据较为严重，可能是发达国家在世界范围内流动的人口较大，但更可能是发达国家能得到有效的检测并报告病例；

In [10]:
def addDailyBar(df) -> Bar:
    province = df.index[1:-2].values.tolist()
    values = df.values[1:-2].astype('int').tolist()
    data = [list(z) for z in zip(province, values)]
    data.sort(key=lambda x:x[1])
    
    bar = (
        Bar(
            init_opts=opts.InitOpts()
        )
        .add_xaxis([t[0] for t in data])
        .add_yaxis('Cumulative Number of Confirmed', [t[1] for t in data])
        .reversal_axis()
        .set_series_opts(label_opts=opts.LabelOpts(position='right'))
        .set_global_opts(
            title_opts=opts.TitleOpts(title='Cumulative number of confirmed COVID-19 in China over provinces', subtitle=df.values[0], pos_left='35%'),
            legend_opts=opts.LegendOpts(pos_right='10%', pos_bottom='10%'),
            tooltip_opts=opts.TooltipOpts(trigger='axis')
        )
    )
    return bar

In [11]:
t = (
    Timeline(init_opts=opts.InitOpts(width='1100px', height='800px'))
    .add_schema(play_interval=500)
)
for date in df.index:
    bar = addDailyBar(df.loc[date])
    t.add(bar, date.date())
t.load_javascript()

In [12]:
t.render('render/Accumulated diagnosis bar.html')

'D:\\编程\\lab\\Data Mining\\render\\Accumulated diagnosis bar.html'

In [13]:
t.render_notebook()

In [14]:
def aggByDate() -> Bar:
    barDf = df.loc[:, '每日新增']
    x_data = df.loc['2020-01-20':'2020-05-01'].index.date.tolist()
    
    bar = (
        Bar()
        .add_xaxis(x_data)
        .add_yaxis(
            series_name='Daily new',
            y_axis=barDf.values.tolist(),
            yaxis_index=0
        )
        .extend_axis(yaxis=opts.AxisOpts())
        .set_series_opts(label_opts=opts.LabelOpts(is_show=False))
        .set_global_opts(
            title_opts=opts.TitleOpts('', pos_left='35%'),
            tooltip_opts=opts.TooltipOpts(trigger='axis', axis_pointer_type='cross'),
            legend_opts=opts.LegendOpts(pos_right='10%', pos_bottom='15%')
        )
    )
    
    lineDf = df.loc[:, '累计确诊']
    line = (
        Line()
        .add_xaxis(x_data)
        .add_yaxis(
            series_name='Cumulative confirmed', 
            y_axis=lineDf.values.tolist(),
            label_opts=opts.LabelOpts(is_show=False),
            yaxis_index=1
        )
    )
    
    bar.overlap(line)
    
    return bar

In [15]:
bar = aggByDate()
bar.load_javascript()

In [16]:
bar.render('render/Daily new Vs Cumulative Confirmed.html')

'D:\\编程\\lab\\Data Mining\\render\\Daily new Vs Cumulative Confirmed.html'

In [17]:
bar.render_notebook()

In [18]:
df = pd.read_csv('data/china-social-news.csv')

In [19]:
df.set_index(pd.to_datetime(df['时间']), inplace=True)
df.dropna(inplace=True)
df.sort_index(inplace=True)

In [20]:
print('Data Amount：', df.shape[0])
print('Data Time Range:', df.index.min().date(), df.index.max().date())

Data Amount： 1334
Data Time Range: 2020-01-26 2020-05-19


In [21]:
df.head(3)

标题          时间  \
时间                                                       
2020-01-26  中国生物多样性保护与绿色发展基金会：向湖北紧急支援4万个口罩  2020-01-26   
2020-01-26                         中国旅行社协会  2020-01-26   
2020-01-26                         中国旅行社协会  2020-01-26   

                                                          URL  \
时间                                                              
2020-01-26  http://www.chinanpo.gov.cn/1944/123496/nextind...   
2020-01-26  http://www.chinanpo.gov.cn/1944/123533/nextind...   
2020-01-26  http://www.chinanpo.gov.cn/1944/123530/nextind...   

                                                         正文内容  \
时间                                                              
2020-01-26  大年三十，中国绿发会紧急采购4万个口罩，支援武汉市和襄阳市，今天首批12000个口罩已到达湖...   
2020-01-26  ：处理行前解约应注意这几点针对新型冠状病毒肺炎疫情，积极响应国家相关部门的通知要求，发挥法律...   
2020-01-26                              ：致境内外旅游供应商、旅游业者的一封公开信   

                           来源  
时间                             
2020-01-26  中国生物多样性保护与绿色发展基金会  
2020-01-26            中国旅行社协会  
2020-01-26            中国旅行社协会

In [22]:
from jieba import analyse
def get_keywords(news_list):
    keywords = []
    for keyword in analyse.extract_tags(''.join(news_list), topK=100, withWeight=True):
        keywords.append(keyword)
    return keywords

In [23]:
from pyecharts import options as opts
from pyecharts.charts import WordCloud
from pyecharts.globals import SymbolType

from pyecharts.globals import CurrentConfig, NotebookType
CurrentConfig.NOTEBOOK_TYPE = NotebookType.JUPYTER_LAB

def render_wordcloud(data, title):
    c = (
        WordCloud()
        .add(series_name="", data_pair=data, word_size_range=[20, 100], shape=SymbolType.ROUND_RECT)
        .set_global_opts(
            title_opts=opts.TitleOpts(
                title=title, title_textstyle_opts=opts.TextStyleOpts(font_size=23)
            ),
            tooltip_opts=opts.TooltipOpts(is_show=True),
        )
    )
    return c

In [24]:
from pyecharts.charts import Timeline

t2 = (
    Timeline(init_opts=opts.InitOpts(width='1100px', height='800px'))
    .add_schema(play_interval=500)
)

In [25]:
def add_to_timeline(data, date):
    keywords = get_keywords(data)
    c = render_wordcloud(keywords, '')
    t2.add(c, date.date())

In [26]:
def get_timeline():
    result = []
    count = 0
    MAX = 80
    date = pd.to_datetime('2020-01-26')
    for date in pd.date_range(start='2020-01-26', end='2020-05-19'):
        try:
            count = count + df.loc[date, '正文内容'].shape[0]
            for item in df.loc[date, '正文内容'].tolist():
                result.append(item)
            if count >= MAX:
                add_to_timeline(result, date)
                result.clear()
                count = 0
        except Exception:
            continue
    if count > 0:
        add_to_timeline(result, date)

In [27]:
get_timeline()

Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\49518\AppData\Local\Temp\jieba.cache
Loading model cost 0.630 seconds.
Prefix dict has been built successfully.


# 中国社会组织公共服务平台疫情防控专区新闻词云可视化

我们通过爬虫技术，对中国社会组织公共服务平台疫情防控专区新闻进行了抓取，共计获得了 1-26 至 5-19 时间段内共1400+新闻；

词云图，也叫文字云，是对文本中出现频率较高的“关键词”予以视觉化的展现，词云图过滤掉大量的低频低质的文本信息，使得浏览者只要一眼扫过文本就可领略文本的主旨。

对该平台上发布的所有文章使用jieba进行分词、获取主题词（取排名前100位），并渲染词云图：

In [28]:
t2.load_javascript()

In [29]:
t2.render('render/Wordcloud.html')

'D:\\编程\\lab\\Data Mining\\render\\Wordcloud.html'

In [30]:
t2.render_notebook()

- 疫情前期主题词以“防控”、“组织”、“工作”、“社会”为主，对应于主要的抗疫力量为政府动员工作和社会组织捐赠
- 从2月末开始，“企业”，“复工”等词语占比越来越大，也对应着复工成为主要需求；

## TF-IDF值
TF-IDF（Term Frequency-InversDocument Frequency）是一种常用于信息处理和数据挖掘的加权技术。该技术采用一种统计方法，根据字词的在文本中出现的次数和在整个语料中出现的文档频率来计算一个字词在整个语料中的重要程度。它的优点是能过滤掉一些常见的却无关紧要本的词语，同时保留影响整个文本的重要字词。

TF - IDF = TF * IDF

TF（Term Frequency）表示某个关键词在整篇文章中出现的频率。IDF（InversDocument Frequency）表示计算倒文本频率。文本频率是指某个关键词在整个语料所有文章中出现的次数。倒文档频率又称为逆文档频率，它是文档频率的倒数，主要用于降低所有文档中一些常见却对文档影响不大的词语的作用。

In [31]:
from pyecharts.charts import Bar

def get_tf_bar(x_data, y_data):
    b = (
        Bar(
            init_opts=opts.InitOpts()
        )
        .add_xaxis(x_data)
        .add_yaxis(
            series_name='',
            y_axis=y_data
        )
        .add_dataset()
        .reversal_axis()
        .set_series_opts(label_opts=opts.LabelOpts(is_show=False))
        .set_global_opts(
            title_opts=opts.TitleOpts(title='TF-IDF Ranking', pos_left='35%'),
            legend_opts=opts.LegendOpts(pos_right='10%', pos_bottom='10%'),
            tooltip_opts=opts.TooltipOpts(trigger='axis')
        )
    )
    return b

In [32]:
keywords = get_keywords(df.loc[:, '正文内容'])
keywords[:10]

[('疫情', 0.22706395346709843),
 ('防控', 0.17074977030094585),
 ('组织', 0.0675057784424657),
 ('捐赠', 0.062243513190542804),
 ('社会', 0.057935903583603246),
 ('工作', 0.057022622823337914),
 ('协会', 0.054245645974525636),
 ('防疫', 0.04727786567173266),
 ('冠状病毒', 0.04383926161901604),
 ('肺炎', 0.04318461971307456)]

In [33]:
x_data = []
y_data = []

for keyword in keywords[:20]:
    x_data.append(keyword[0])
    y_data.append(keyword[1])
    
x_data.reverse()
y_data.reverse()

In [34]:
b = get_tf_bar(x_data, y_data)

In [35]:
b.load_javascript()

In [36]:
b.render('render/TF-IDF.html')

'D:\\编程\\lab\\Data Mining\\render\\TF-IDF.html'

In [37]:
b.render_notebook()

输出结果如下图所示，可以看到“疫情”、“组织”、“捐赠”、“社会”、“协会”、“肺炎”、“物资”等都是高频词，也是大众普 遍关心的主题。